In [1]:
with open("/opt/etherpad/APIKEY.txt") as f:
    api_key = f.read()

In [2]:
print (api_key)

029ff291f1256972b277789579ce5e29e83b6bbd52e319fe49af198c35013e9b


In [3]:
api_url = "https://hub.xpub.nl/soupboat/pad/api/1.2.15/"

In [4]:
print (api_url)

https://hub.xpub.nl/soupboat/pad/api/1.2.15/


In [5]:
from urllib.request import urlopen
from urllib.parse import urlencode
import json

def ep(api_url, api_key, fn, **apiargs):
    apiargs['api_key'] = api_key
    return json.load(urlopen(f"{api_url}{fn}", data=urlencode(apiargs).encode()))

Functions can also return functions, this trick is used to make a function (this kind of function sometimes called a "factory"), that you can call without having to repeat the api_url + api+key variables.

In [6]:
# a function can return a function :)
def make_etherpad_api(api_url, api_key):
    def call(fn, **apiargs):
        apiargs['api_key'] = api_key
        return json.load(urlopen(f"{api_url}{fn}", data=urlencode(apiargs).encode()))
    return call

In [7]:
pad = make_etherpad_api(api_url, api_key)

In [8]:
pad("listAllPads")

{'code': 0,
 'message': 'ok',
 'data': {'padIDs': ['???',
   'CcnxKtsc6MB14S964ZHI',
   'XNf5qq9A85k3S1kpvh2I',
   'ahahahahah',
   'alnik-petitions',
   'alnik-petitions-processed',
   'amphibia.web',
   'api',
   'blibli',
   'bootleg',
   'bootleg-florensky',
   'camillo_glossary',
   'camilo-glossary',
   'camilo_glossary',
   'documentation-CME',
   "don't_see_this_please",
   'garside',
   'glossary',
   'habitat',
   'helloXPUBIES',
   'hellohellohellocheckcheck',
   'input',
   'input_etc',
   'isitworking',
   'japoco',
   'markdown.try',
   'mbm2LakBJiPBIc9t5Pqy',
   'meh',
   'nameofapad',
   'newest_padddd',
   'noooooooooo',
   'output',
   'output_etc',
   'paddy',
   'sp_emergency_meeting',
   'test',
   'test123',
   'this-is-a-new-pad-eheh',
   'why-publish-noise',
   'wooow',
   'xpubpizza',
   'yeeeees',
   'yesssss',
   'yoho',
   'zzz']}}

## Ether-Chat!

To just use the bot, skip to the cell that defines the function **make_etherchat_bot**

https://etherpad.org/doc/latest/#index_chat

* getChatHistory (padid, [start, end])
* getChatHead (padid)
* appendChatMessage (padid, authorid, text, [time])

* sendClientsMessage("test", "testing")

In [9]:
pad("sendClientsMessage", padID="test", msg="testing") 

{'code': 0, 'message': 'ok', 'data': None}

In [10]:
pad("appendChatMessage", padID="test", text="Hello")

{'code': 0, 'message': 'ok', 'data': None}

In [11]:
pad("getChatHead", padID="test")

{'code': 0, 'message': 'ok', 'data': {'chatHead': 2}}

In [12]:
pad("getChatHistory", padID="test")

{'code': 0,
 'message': 'ok',
 'data': {'messages': [{'text': 'what time is it?',
    'userId': 'a.pWdd5biNjDAJQot6',
    'time': 1636908576766,
    'userName': None},
   {'text': 'The time is now 16:49:38',
    'userId': 'a.JncA1N8gj7bhrPBS',
    'time': 1636908578927,
    'userName': 'timebot'},
   {'text': 'Hello', 'time': 1636965977319, 'userName': None}]}}

In [13]:
pad("getChatHistory", padID="test", start=1, end=2)

{'code': 0,
 'message': 'ok',
 'data': {'messages': [{'text': 'The time is now 16:49:38',
    'userId': 'a.JncA1N8gj7bhrPBS',
    'time': 1636908578927,
    'userName': 'timebot'},
   {'text': 'Hello', 'time': 1636965977319, 'userName': None}]}}

In [14]:
from time import sleep

In [15]:
pad_id="test"

In [16]:
author_id = None
if author_id == None:
    r = pad("createAuthor", name="etherchat")
    author_id = r['data']['authorID']

In [17]:
chat_head = None
r = pad("getChatHead", padID=pad_id)
if r['code'] == 0:
    chat_head = r['data']['chatHead']
    print (f"Initial chat_head is {chat_head}")
while True:
    # print ("checking chat history")
    r = pad("getChatHistory", padID="test", start=chat_head+1, end=chat_head+1)
    if r['code'] == 0:
        chat_head = chat_head + 1
        msg = r['data']['messages'][0]
        print (f"new message {msg}")
        if msg['userId'] and msg['userId'] == author_id:
            print ("ignoring my own message")
            continue
        userName, text = msg['userName'], msg['text']
        print (f"new message from {userName}: {text}")
        pad("appendChatMessage", padID=pad_id, authorID=author_id, text=f"huh huh, {userName} said {text}")
        # chat_head += 1
    sleep(2.5)

Initial chat_head is 2


KeyboardInterrupt: 

Now, let's make a function to abstract this "bot" behaviour. To separate the actual behavior of the bot (and make it customizable), we give this function a function that takes a pad and a message and (optionally) returns a response.

## make_etherchat_bot

In [18]:
from time import sleep

def make_etherchat_bot(pad, pad_id, bot_name, bot, sleep_time=2.5):
    print (f"Etherchat bot running... in pad: {pad_id}")
    author_id = None
    if author_id == None:
        r = pad("createAuthor", name=bot_name)
        author_id = r['data']['authorID']
    chat_head = None
    r = pad("getChatHead", padID=pad_id)
    if r['code'] == 0:
        chat_head = r['data']['chatHead']
        # print (f"Initial chat_head is {chat_head}")
    while True:
        r = pad("getChatHistory", padID="test", start=chat_head+1, end=chat_head+1)
        if r['code'] == 0:
            chat_head = chat_head + 1
            msg = r['data']['messages'][0]
            # print (f"new message {msg}")
            if msg['userId'] and msg['userId'] == author_id:
                # print ("ignoring my own message")
                continue
            userName, text = msg['userName'], msg['text']
            # call the bot function
            bot(msg, pad, pad_id, bot_name, author_id)
        sleep(sleep_time)

## timekeeping bot

A "hello world" bot: Say "time" in the chat and the bot responds (in the chat) with the time.

In [19]:
import datetime

def timekeeping_bot (msg, pad, pad_id, bot_name, bot_author_id):
    if "time" in msg['text'].lower():
        t = datetime.datetime.now()
        time_formatted = t.strftime("%H:%M:%S")
        pad("appendChatMessage", padID=pad_id, authorID=bot_author_id, text=f"The time is now {time_formatted}")

Put it all together, **NB this cell stays running until you STOP it** (and blocks the rest of the notebook until you do so)...

In [20]:
make_etherchat_bot(pad, "test", "timebot", timekeeping_bot)

Etherchat bot running... in pad: test


KeyboardInterrupt: 

Check it out here: https://hub.xpub.nl/soupboat/pad/p/test